In [1]:
import spot, buddy
spot.setup()

Read input NBA:

In [2]:
aut = spot.automaton('converted_req_grant_3.hoa')
#display(aut)  # it is too large to be displayed
print("num_states: {}, num edges: {}".format(aut.num_states(), aut.num_edges()))

num_states: 120, num edges: 3463


Determinize to DPA:

In [3]:
det = aut.postprocess('deterministic', 'parity', 'low')  # takes 1min
#display(det)
print("num_states: {}, num edges: {}".format(det.num_states(), det.num_edges()))
print(spot.bdd_to_formula(det.ap_vars(), det.get_dict()))

num_states: 1124, num edges: 12379329
g & in_eq_rs1 & in_eq_rs2 & in_eq_rs3 & in_l_rs1 & in_l_rs2 & in_l_rs3 & in_save_rs1 & in_save_rs2 & in_save_rs3 & out_rs1 & out_rs2 & out_rs3 & req


Define controlable APs:

In [4]:
outputs_bdd = buddy.bdd_ithvar(det.register_ap("in_save_rs3"))
for o in ("out_rs3", "in_save_rs2", "out_rs2", "in_save_rs1", "out_rs1", "g"):
    outputs_bdd = outputs_bdd & buddy.bdd_ithvar(det.register_ap(o))
spot.set_synthesis_outputs(det, outputs_bdd)
#display(det)

Turn into a game:

In [5]:
game = spot.split_2step(det, spot.get_synthesis_outputs(det), False)
#display(game)

Solve game:

In [6]:
# calling this method results in
#   RuntimeError: solve_parity_game(): arena must be colorized
spot.solve_game(game)

RuntimeError: solve_parity_game(): arena must be colorized

In [ ]:
spot.highlight_strategy(game)
display(game)

Extract winning strategy:

In [ ]:
m = spot.solved_game_to_separated_mealy(game)
display(m)

In [ ]:
spot.mealy_machine_to_aig(m, "isop")